In [0]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import (
    StringIndexer,
    OneHotEncoder,
    VectorAssembler
)
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.sql import functions as F


In [0]:
# Databricks notebook source
import random
import math
from pyspark.sql import functions as F
from pyspark.sql.types import (
    StructType, StructField,
    LongType, IntegerType, StringType, DoubleType
)

# =========================
# 0) 参数
# =========================
SEED = 42
N = 50_000   # Python loop 建议 <= 100k；你可先 20k 试跑

random.seed(SEED)

# =========================
# 1) 显式声明 schema（你要求的）
# =========================
schema = StructType([
    StructField("app_id", LongType(), False),

    StructField("age", IntegerType(), False),
    StructField("province", StringType(), False),
    StructField("employment_type", StringType(), False),

    StructField("income_annual", DoubleType(), False),
    StructField("credit_score", DoubleType(), False),
    StructField("dti", DoubleType(), False),
    StructField("utilization", DoubleType(), False),

    StructField("delinq_12m", IntegerType(), False),
    StructField("num_cards", IntegerType(), False),
    StructField("requested_limit", IntegerType(), False),

    StructField("risk_score", DoubleType(), False),
    StructField("p_approve", DoubleType(), False),
    StructField("approve", IntegerType(), False),
])

# =========================
# 2) helper functions
# =========================
def clamp(x, lo, hi):
    return max(lo, min(x, hi))

# =========================
# 3) Python loop 生成数据（deterministic）
# =========================
provinces = ["ON", "BC", "AB", "QC", "MB", "NS"]
employment_types = ["Salaried", "SelfEmployed", "Student", "Unemployed"]

rows = []

for app_id in range(N):

    # demographics
    age = random.randint(18, 72)
    province = random.choice(provinces)
    employment_type = random.choice(employment_types)

    # income (lognormal-ish)
    income_raw = math.exp(random.random() * 2.0 + 10.2)
    if employment_type == "Student":
        income_annual = income_raw * 0.35
    elif employment_type == "Unemployed":
        income_annual = income_raw * 0.15
    else:
        income_annual = income_raw
    income_annual = clamp(income_annual, 15_000.0, 350_000.0)

    # credit score
    credit_score = 300.0 + random.random() * 550.0
    if employment_type == "Salaried":
        credit_score += 35.0
    elif employment_type == "SelfEmployed":
        credit_score += 10.0
    elif employment_type == "Student":
        credit_score -= 30.0
    else:
        credit_score -= 60.0
    credit_score += (age - 35) * 0.8
    credit_score = clamp(credit_score, 300.0, 850.0)

    # core risk features
    dti = random.random() * 1.2
    if income_annual < 45_000.0:
        dti *= 1.15
    dti = clamp(dti, 0.0, 1.2)

    utilization = random.random() * 1.5
    if credit_score < 600.0:
        utilization *= 1.15
    utilization = clamp(utilization, 0.0, 1.5)

    delinq_12m = int(random.random() * 2.5)
    if credit_score < 580.0:
        delinq_12m += int(random.random() * 3.0)
    delinq_12m = min(delinq_12m, 6)

    num_cards = int(random.random() * 6.0)
    if age > 45:
        num_cards += int(random.random() * 3.0)
    num_cards = min(num_cards, 8)

    requested_limit = random.randint(1_000, 30_000)

    # approval policy -> risk_score
    risk_score = 0.0

    # credit score bucket
    if credit_score < 560.0:
        risk_score += 2.2
    elif credit_score < 620.0:
        risk_score += 1.4
    elif credit_score < 680.0:
        risk_score += 0.8
    else:
        risk_score += 0.2

    # DTI bucket
    if dti > 0.55:
        risk_score += 1.6
    elif dti > 0.40:
        risk_score += 0.9
    else:
        risk_score += 0.2

    # utilization bucket
    if utilization > 0.95:
        risk_score += 1.2
    elif utilization > 0.70:
        risk_score += 0.7
    else:
        risk_score += 0.2

    # delinquency
    risk_score += delinq_12m * 0.55

    # employment adjustments
    if employment_type == "Unemployed":
        risk_score += 1.8
    elif employment_type == "Student":
        risk_score += 0.9
    elif employment_type == "SelfEmployed":
        risk_score += 0.35

    # income adjustments
    if income_annual < 35_000.0:
        risk_score += 0.9
    elif income_annual < 50_000.0:
        risk_score += 0.4

    # requested limit adjustments
    if requested_limit > 20_000:
        risk_score += 0.35

    # risk_score -> p_approve (sigmoid-ish)
    a, b = 1.15, 2.4
    p_approve = 1.0 / (1.0 + math.exp(a * (risk_score - b)))

    # noise override
    if random.random() < 0.02:
        p_approve = 0.5

    approve = 1 if random.random() < p_approve else 0

    # IMPORTANT: 按 schema 顺序写 tuple（避免 dict 顺序问题）
    rows.append((
        int(app_id),

        int(age),
        str(province),
        str(employment_type),

        float(round(income_annual, 2)),
        float(round(credit_score, 1)),
        float(round(dti, 3)),
        float(round(utilization, 3)),

        int(delinq_12m),
        int(num_cards),
        int(requested_limit),

        float(round(risk_score, 3)),
        float(round(p_approve, 6)),
        int(approve),
    ))

# =========================
# 4) 创建 Spark DataFrame（强制 schema）
# =========================
df = spark.createDataFrame(rows, schema=schema)

df.printSchema()
df.show(5, truncate=False)

# =========================
# 5) sanity checks
# =========================
df.groupBy("approve").count().show()

df.select(
    F.avg("income_annual").alias("avg_income"),
    F.avg("credit_score").alias("avg_score"),
    F.avg("dti").alias("avg_dti"),
    F.avg("utilization").alias("avg_util"),
    F.avg("delinq_12m").alias("avg_delinq"),
    F.avg("p_approve").alias("avg_p_approve"),
).show()

# 额外：批准率在不同信用分段
(df
 .withColumn("score_bucket",
             F.when(F.col("credit_score") < 560, "<560")
              .when(F.col("credit_score") < 620, "560-619")
              .when(F.col("credit_score") < 680, "620-679")
              .otherwise(">=680"))
 .groupBy("score_bucket")
 .agg(F.avg("approve").alias("approval_rate"), F.count("*").alias("n"))
 .orderBy("score_bucket")
 .show()
)


root
 |-- app_id: long (nullable = false)
 |-- age: integer (nullable = false)
 |-- province: string (nullable = false)
 |-- employment_type: string (nullable = false)
 |-- income_annual: double (nullable = false)
 |-- credit_score: double (nullable = false)
 |-- dti: double (nullable = false)
 |-- utilization: double (nullable = false)
 |-- delinq_12m: integer (nullable = false)
 |-- num_cards: integer (nullable = false)
 |-- requested_limit: integer (nullable = false)
 |-- risk_score: double (nullable = false)
 |-- p_approve: double (nullable = false)
 |-- approve: integer (nullable = false)

+------+---+--------+---------------+-------------+------------+-----+-----------+----------+---------+---------------+----------+---------+-------+
|app_id|age|province|employment_type|income_annual|credit_score|dti  |utilization|delinq_12m|num_cards|requested_limit|risk_score|p_approve|approve|
+------+---+--------+---------------+-------------+------------+-----+-----------+----------+-------

In [0]:
df.display()

app_id age province employment_type income_annual credit_score dti utilization delinq_12m num_cards requested_limit risk_score p_approve approve 0 58 ON Salaried 118551.29 488.1 0.167 0.177 2 3 4070 3.7 0.183172 0 1 19 MB SelfEmployed 112649.81 682.9 0.503 0.674 0 5 25864 2.0 0.613014 0 2 39 AB SelfEmployed 41383.09 733.1 0.141 0.57 0 2 9667 1.35 0.769856 1 3 52 ON Unemployed 15000.0 414.8 0.868 1.5 0 1 26331 8.05 0.001505 0 4 32 ON Unemployed 15000.0 587.2 0.503 0.639 0 1 23398 5.55 0.026021 0 5 28 MB SelfEmployed 37302.1 513.1 1.2 1.104 3 5 26427 7.75 0.002124 0 6 69 AB Unemployed 15000.0 383.2 1.2 1.5 1 4 16035 8.25 0.001196 0 7 65 MB Student 41948.82 529.6 0.805 0.624 2 4 29216 6.75 0.006676 0 8 68 NS Unemployed 15000.0 478.0 0.822 0.807 1 7 4753 7.75 0.002124 0 9 35 NS Student 15000.0 509.1 0.626 1.5 2 3 6854 7.9 0.001788 0 10 58 AB SelfEmployed 36522.31 747.8 0.744 1.168 1 0 1638 4.3 0.101106 0 11 71 AB SelfEmployed 30207.65 821.7 1.2 0.128 1 2 26094 4.15 0.117897 0 12 53 BC Student 27052.25 618.0 1.2 1.393 1 6 14074 6.55 0.008388 0 13 46 MB Unemployed 15000.0 372.4 0.467 1.015 0 1 8501 7.0 0.005016 0 14 39 ON SelfEmployed 46955.45 580.2 0.647 1.248 2 3 8962 6.05 0.01481 0 15 30 ON Salaried 100505.28 525.9 0.493 1.49 1 3 2986 4.85 0.056386 0 16 24 BC SelfEmployed 39356.55 547.9 0.582 0.48 2 2 29224 6.2 0.012493 0 17 59 MB Salaried 186837.12 850.0 1.018 0.249 1 2 2921 2.55 0.456982 1 18 42 AB Unemployed 15000.0 628.7 1.008 1.175 1 2 7222 6.85 0.005955 0 19 55 NS Salaried 120084.52 382.4 0.701 0.867 2 5 7089 5.6 0.024602 0 20 33 QC Salaried 176873.89 646.7 0.695 0.06 0 3 19521 2.6 0.442752 0 21 31 NS Student 15177.2 484.5 0.927 0.517 2 0 16017 6.9 0.005624 0 22 24 ON SelfEmployed 73996.23 374.1 0.419 0.119 0 2 18800 3.65 0.191933 0 23 69 NS Salaried 102306.29 667.2 1.118 0.155 2 3 25327 4.05 0.130392 0 24 56 BC Student 15000.0 635.6 0.364 0.733 2 5 14879 4.6 0.073782 1 25 39 BC Student 15000.0 516.2 0.974 0.968 2 4 5884 7.9 0.001788 0 26 55 MB SelfEmployed 63549.44 349.0 0.438 1.5 2 4 22854 6.1 0.013994 0 27 44 MB SelfEmployed 171360.99 447.4 0.195 1.38 1 1 11885 4.5 0.082036 0 28 60 NS SelfEmployed 45872.06 763.1 0.13 1.308 2 3 16083 3.45 0.230144 0 29 32 BC Salaried 100716.65 551.8 0.334 0.12 2 3 23266 4.05 0.130392 0 30 19 ON Student 15000.0 786.6 0.366 0.163 1 4 11278 2.95 0.346944 0 31 25 QC SelfEmployed 44776.78 691.8 0.002 1.388 1 4 25312 3.25 0.273388 1 32 45 ON Student 32744.45 642.9 0.172 1.35 1 4 11688 4.55 0.077809 0 33 26 BC Unemployed 15256.16 441.3 1.032 0.3 2 5 10957 7.8 0.002005 0 34 55 MB Student 23864.67 529.2 0.295 0.816 4 1 17890 7.1 0.004474 0 35 23 BC Student 15000.0 369.9 0.034 0.422 3 0 14580 6.05 0.01481 0 36 63 NS Unemployed 15000.0 396.6 0.905 0.01 3 1 6763 8.35 0.001066 0 37 47 ON SelfEmployed 168541.96 386.3 0.16 0.802 2 3 15502 4.55 0.077809 0 38 50 QC Unemployed 24277.28 661.0 0.655 0.389 0 5 18081 5.3 0.03439 0 39 46 ON Student 15050.48 463.5 1.2 0.139 1 0 14594 6.35 0.010535 0 40 44 ON SelfEmployed 142312.74 531.4 0.924 1.5 2 3 16629 6.45 0.5 1 41 66 QC Unemployed 15000.0 668.8 1.104 1.347 1 2 13742 6.85 0.005955 0 42 43 NS SelfEmployed 144496.61 822.1 1.177 0.801 2 3 22725 4.3 0.101106 0 43 26 QC SelfEmployed 29749.55 511.3 0.292 0.564 2 4 28260 5.3 0.03439 0 44 48 ON Salaried 198752.51 537.9 0.78 1.348 3 5 1667 6.65 0.007484 0 45 48 NS Salaried 83111.57 465.3 0.839 1.323 1 4 27846 5.9 0.01755 0 46 55 ON Student 29785.33 785.4 0.518 1.412 0 5 8957 4.1 0.124009 0 47 72 NS Salaried 132250.67 675.9 0.049 0.799 1 1 1414 2.25 0.543018 0 48 24 QC Student 33568.66 717.0 0.976 0.653 1 5 9850 4.35 0.095998 0 49 67 QC Unemployed 15000.0 667.7 0.37 1.278 2 2 8990 6.0 0.015673 0 50 60 QC Student 15000.0 758.0 0.251 0.318 1 4 23976 3.3 0.262116 0 51 51 BC Salaried 43595.63 571.3 0.766 0.415 3 2 10641 5.25 0.036351 0 52 37 NS Student 24262.78 563.6 0.587 1.287 2 1 9237 7.1 0.004474 0 53 38 ON SelfEmployed 39461.55 718.6 0.382 0.884 1 3 4294 2.4 0.5 1 54 41 BC Student 15000.0 568.6 0.379 1.5 3 0 29457 6

In [0]:
label_col = "approve"

cat_cols = [
    "province",
    "employment_type"
]

num_cols = [
    "age",
    "income_annual",
    "credit_score",
    "dti",
    "utilization",
    "delinq_12m",
    "num_cards",
    "requested_limit"
]


In [0]:
train_df, test_df = df.randomSplit([0.8, 0.2], seed=42)

print("train:", train_df.count())
print("test :", test_df.count())


train: 40145
test : 9855


In [0]:
indexers = [
    StringIndexer(
        inputCol=c,
        outputCol=f"{c}_idx",
        handleInvalid="keep"
    )
    for c in cat_cols
]

encoder = OneHotEncoder(
    inputCols=[f"{c}_idx" for c in cat_cols],
    outputCols=[f"{c}_ohe" for c in cat_cols]
)


In [0]:
assembler = VectorAssembler(
    inputCols=num_cols + [f"{c}_ohe" for c in cat_cols],
    outputCol="features",
    handleInvalid="keep"
)


In [0]:
dt = DecisionTreeClassifier(
    labelCol=label_col,
    featuresCol="features",
    maxDepth=5,              # 控制可解释性（很关键）
    minInstancesPerNode=200, # 防止过拟合，像 policy
    seed=42
)


In [0]:
pipeline = Pipeline(
    stages=indexers + [encoder, assembler, dt]
)


dt_model = pipeline.fit(train_df)


In [0]:
import mlflow
from pyspark.sql import functions as F
from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer, OneHotEncoder, VectorAssembler
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.mllib.evaluation import MulticlassMetrics

In [0]:
label_col = "approve"
pred_col = "prediction"
positive_label = 1.0   # ✅ 银行里你可以改成 0.0（例如把“拒绝/坏客户”当正类）
label_col = "approve"
seed = 42


In [0]:
sample_output_sdf.display()

prediction probability 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7223230490018149, 0.2776769509981851)) 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.31030444964871196, 0.689695550351288)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7223230490018149, 0.2776769509981851)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.883550263085018, 0.116449736914982)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7223230490018149, 0.2776769509981851)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.883550263085018, 0.116449736914982)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7223230490018149, 0.2776769509981851)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7223230490018149, 0.2776769509981851)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.883550263085018, 0.116449736914982)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6538461538461539, 0.34615384615384615)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.883550263085018, 0.116449736914982)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6538461538461539, 0.34615384615384615)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.883550263085018, 0.116449736914982)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.883550263085018, 0.116449736914982)) 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9473087104500189, 0.05269128954998109)) 0.0 Map(vectorType -> dense, length -> 2,

In [0]:
from pyspark.ml.functions import vector_to_array

In [0]:
with mlflow.start_run(run_name="dt_cc_approval") as run:
    # ---- train
    model = pipeline.fit(train_df)

    # ---- predict
    pred_df = model.transform(test_df)

    # ---- AUC (threshold-free)
    auc = BinaryClassificationEvaluator(
        labelCol=label_col,
        rawPredictionCol="rawPrediction",
        metricName="areaUnderROC"
    ).evaluate(pred_df)

    # ---- Accuracy/Precision/Recall/F1 for chosen positive label
    rdd = pred_df.select("prediction", label_col).rdd.map(lambda r: (float(r["prediction"]), float(r[label_col])))
    m = MulticlassMetrics(rdd)

    accuracy = m.accuracy
    precision = m.precision(positive_label)
    recall = m.recall(positive_label)
    f1 = m.fMeasure(positive_label)

    # ---- log metrics
    mlflow.log_metric("AUC", float(auc))
    mlflow.log_metric("Accuracy", float(accuracy))
    mlflow.log_metric(f"Precision_pos{int(positive_label)}", float(precision))
    mlflow.log_metric(f"Recall_pos{int(positive_label)}", float(recall))
    mlflow.log_metric(f"F1_pos{int(positive_label)}", float(f1))

    # ---- log params (optional but useful)
    mlflow.log_params({
        "algo": "DecisionTree",
        "maxDepth": 5,
        "minInstancesPerNode": 200,
        "positive_label": int(positive_label),
        "seed": seed
    })

    # ---- signature (production contract)
    # input = model raw input columns (drop label); include only cols model expects
    input_cols = ["age","province","employment_type","income_annual","credit_score","dti","utilization","delinq_12m","num_cards","requested_limit"]
    sample_input_sdf = df.select(*input_cols).limit(200)
    # sample_output_sdf = model.transform(sample_input_sdf).select("prediction", "probability")
    sample_output_sdf = (
    dt_model.transform(sample_input_sdf)
    .select(
        F.col("prediction").cast("double").alias("prediction"),
        vector_to_array("probability").alias("probability")   # ✅ Array[Double]
    )
)

    signature = infer_signature(
        sample_input_sdf.toPandas(),
        sample_output_sdf.toPandas()
    )
    input_example = sample_input_sdf.limit(5).toPandas()

    # ---- log model to this run (artifact path = model)
    mlflow.spark.log_model(
        spark_model=model,
        artifact_path="dt_cc_model",
        registered_model_name="dbx.default.dt_cc_model",
        signature=signature,
        input_example=input_example
    )

    


/databricks/spark/python/pyspark/sql/context.py:165: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(
/databricks/python/lib/python3.12/site-packages/mlflow/types/utils.py:452: UserWarning: Hint: Inferred schema contains integer column(s). Integer columns in Python cannot represent missing values. If your input data contains missing values at inference time, it will be encoded as floats and will cause a schema enforcement error. The best way to avoid this problem is to infer the model schema based on a realistic data sample (training dataset) that includes missing values. Alternatively, you can declare integer columns as doubles (float64) whenever these columns may have missing values. See `Handling Integers With Missing Values <https://www.mlflow.org/docs/latest/models.html#handling-integers-with-missing-values>`_ for more details.
  warnings.warn(
2026/01/08 04:14:42 INFO mlflow.spark: Inferring pip requirements by reloading the log

2026/01/08 04:15:15 WARNING mlflow.utils.environment: Encountered an unexpected error while inferring pip requirements (model URI: dbfs:/databricks/mlflow-tracking/4417723288018435/97d3535a81f14977af84ecc6c565d334/artifacts/dt_cc_model/sparkml, flavor: spark). Fall back to return ['pyspark==4.0.0']. Set logging level to DEBUG to see the full traceback. 


Uploading artifacts:   0%|          | 0/6 [00:00<?, ?it/s]

Registered model 'dbx.default.dt_cc_model' already exists. Creating a new version of this model...


Uploading artifacts:   0%|          | 0/56 [00:00<?, ?it/s]

🔗 Created version '3' of model 'dbx.default.dt_cc_model': https://adb-7405605317278017.17.azuredatabricks.net/explore/data/models/dbx/default/dt_cc_model/version/3?o=7405605317278017
